In [2]:
import plotly as py
import plotly.graph_objs as go
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from scipy.interpolate import CubicSpline
import sklearn.datasets
import umap
from sklearn.decomposition import PCA
from sklearn.manifold import MDS
import plotly.express as px
from fuzzywuzzy import fuzz

In [23]:
# Realiza la reducción de dimensión de los datos ingresados con el algoritmo seleccionado
def GenDataFrame(nombre_dataframe, separacion=';', IC=0, algoritmo='UMAP'):
    df = pd.read_csv(nombre_dataframe, sep=separacion, index_col=IC)
    
    # Selección del algoritmo de reducción de dimensionalidad
    if algoritmo == 'UMAP':
        reducer = umap.UMAP(min_dist=0.9)
    elif algoritmo == 'PCA':
        reducer = PCA(n_components=2)
    elif algoritmo == 'MDS':
        reducer = MDS(n_components=2)
    else:
        raise ValueError("Algoritmo no soportado. Use 'UMAP', 'PCA' o 'MDS'.")

    # Aplicación del algoritmo seleccionado
    Share = reducer.fit_transform(df)

    dftS = pd.DataFrame(Share, index=df.index, columns=['D1', 'D2'])
    dftS['Y'] = dftS.index
    return dftS

# Función para encontrar grupos de strings similares dentro de la columna seleccionada
def find_similar_groups(column,umbra):
    # Crear un diccionario para almacenar los grupos
    groups = {}

    # Iterar sobre cada índice y valor en la columna
    for index, value in column.items():
        # Buscar grupos similares
        found = False
        for group, members in groups.items():
            for member in members:
                similarity = fuzz.WRatio(value[4:], member[4:])
                if similarity > umbra:  # Puedes ajustar este umbral según las necesidades
                    groups[group].append(value)
                    found = True
                    break
            if found:
                break

        # Si no se encuentra en ningún grupo existente, crear un nuevo grupo
        if not found:
            groups[value] = [value]

    return groups

def Grupos(similar_groups,dftS,colname='Y'):
    DFGrupos = []
    for group, members in similar_groups.items():
        DFGrupos.append(dftS[dftS[colname].isin(members)])
    
    return DFGrupos

def GraficoGrupos(dftS,DFGrupos,resolucion = 10000,ColName='Y'):
    
    NameGrups = [i.split('_')[1] for i in similar_groups.keys()]
    Contador = 0
    # Crear el gráfico con Plotly
    fig = go.Figure()
    
    # Agregar puntos de datos
    fig.add_trace(go.Scatter(x=dftS['D1'], y=dftS['D2'], mode='markers', text = dftS[ColName], name='Puntos', marker=dict(color='gray')))
    
    # Crear una spline cúbica para suavizar la curva
    for DFgrupo in DFGrupos:
        spline_x = CubicSpline(range(len(DFgrupo['D1'])), DFgrupo['D1'])
        spline_y = CubicSpline(range(len(DFgrupo['D2'])), DFgrupo['D2'])

        # Nuevos puntos para la curva suavizada
        t_smooth = np.linspace(0, len(DFgrupo['D1'])-1, resolucion)

        # Evaluar la spline cúbica en los nuevos puntos
        x_smooth = spline_x(t_smooth)
        y_smooth = spline_y(t_smooth)

        # Agregar curva suavizada
        fig.add_trace(go.Scatter(x=x_smooth, y=y_smooth, mode='lines', name=NameGrups[Contador]))
        Contador += 1
        
    # Diseñar el diseño del gráfico
    fig.update_layout(title='Curva de datos',
                      xaxis_title='D1',
                      yaxis_title='D2',
                      showlegend=True)

    # Mostrar el gráfico
    return fig.show()

In [24]:
dftS = GenDataFrame('G7_Share.txt',separacion = ';',IC=0, algoritmo = 'UMAP')

#Solo en caso de ser necesarios si es que no se cuenta con una 
similar_groups = find_similar_groups(dftS['Y'],umbra=80)

DFGroups = Grupos(similar_groups,dftS,colname='Y')
GraficoGrupos(dftS,DFGroups)